In [12]:
import os
import json

# Load setting from Json outside of project.
f = open('../../env/ai.json')
settingsJson = json.load(f)
del f

for key in settingsJson:
    os.environ[key] = settingsJson[key]
    
del settingsJson
    
# # OR manually set them
# os.environ['REQUESTS_CA_BUNDLE'] = '../../env/ZCert.pem'
# os.environ['HUGGING_FACE_API_KEY'] = 'Get here: https://huggingface.co/settings/tokens'
# os.environ['OPENAI_API_KEY'] = 'Get here: https://platform.openai.com/account/api-keys'
# os.environ["SERPAPI_API_KEY"] = 'serpapi KEY, Get here: https://serpapi.com/manage-api-key'

# Setup Web Crawler and Lookup functions

In [13]:
import requests
from bs4 import BeautifulSoup
import json

def remove_keys(dictionary: dict, keyList: list):
    for key in keyList:        
        if key in dictionary:
            del dictionary[key]    

def get_recipe_as_json(url: str) -> dict: 
    url = url.replace("'", "").replace('"', '')
    html = requests.get(url).text   
    soup = BeautifulSoup(html)
    script = soup.find_all("script", {"id": "allrecipes-schema_1-0"})

    recipeDict = json.loads(script[0].text)[0]
    remove_keys(recipeDict, ['review', 'image', 'mainEntityOfPage', 'publisher'])
    # del recipeDict['review']
    # del recipeDict['image']
    # del recipeDict['mainEntityOfPage']
    # del recipeDict['publisher']
    
    return recipeDict

# url = "https://www.allrecipes.com/recipe/212498/easy-chicken-and-broccoli-alfredo/"
# obj = get_recipe_as_json(url)

# Static recipe lists

In [14]:
dessertList = [
   {
      "title": "Chocolate Snack Cake",
      "url": "https://www.allrecipes.com/chocolate-snack-cake-recipe-8350343"
   },
   {
      "title": "Charred Spiced Pears with Smoky Vanilla Cherry Sauce",
      "url": "https://www.allrecipes.com/charred-spiced-pears-with-smoky-vanilla-cherry-sauce-recipe-8347080"
   },
   {
      "title": "Meringue Topped Banana Pudding",
      "url": "https://www.allrecipes.com/meringue-topped-banana-pudding-recipe-8347040"
   },
   {
      "title": "White Chocolate Cinnamon Toast Crunch Bars",
      "url": "https://www.allrecipes.com/white-chocolate-cinnamon-toast-crunch-bars-recipe-7556790"
   },
   {
      "title": "Plum Cobbler for Two",
      "url": "https://www.allrecipes.com/plum-cobbler-for-two-recipe-8304143"
   },
   {
      "title": "Pumpkin Cheesecake Cookies",
      "url": "https://www.allrecipes.com/pumpkin-cheesecake-cookies-recipe-7972485"
   },
   {
      "title": "Chocolate Whipped Cottage Cheese",
      "url": "https://www.allrecipes.com/chocolate-whipped-cottage-cheese-recipe-8303272"
   },
   {
      "title": "Nutella Ice Cream",
      "url": "https://www.allrecipes.com/nutella-ice-cream-recipe-7508716"
   },
   {
      "title": "3-Ingredient Banana Oatmeal Cookies",
      "url": "https://www.allrecipes.com/3-ingredient-banana-oatmeal-cookies-recipe-7972686"
   },
   {
      "title": "Caramel Apple Pie Cookies",
      "url": "https://www.allrecipes.com/caramel-apple-pie-cookies-recipe-7642173"
   }
]

chickenDishList = [
   {
      "title": "Crispy Roasted Chicken",
      "url": "https://www.allrecipes.com/recipe/228363/crispy-roasted-chicken/"
   },
   {
      "title": "Roasted Spatchcocked Chicken With Potatoes",
      "url": "https://www.allrecipes.com/recipe/254877/roasted-spatchcocked-chicken-with-potatoes/"
   },
   {
      "title": "Easy Baked Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/235153/easy-baked-chicken-thighs/"
   },
   {
      "title": "Crispy Baked Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/258878/crispy-baked-chicken-thighs/"
   },
   {
      "title": "Crispy and Tender Baked Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/235151/crispy-and-tender-baked-chicken-thighs/"
   },
   {
      "title": "Million Dollar Chicken",
      "url": "https://www.allrecipes.com/recipe/233953/million-dollar-chicken/"
   },
   {
      "title": "Simple Whole Roasted Chicken",
      "url": "https://www.allrecipes.com/recipe/70679/simple-whole-roasted-chicken/"
   },
   {
      "title": "Beer Can Chicken",
      "url": "https://www.allrecipes.com/recipe/214618/beer-can-chicken/"
   },
   {
      "title": "Air Fryer Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/272858/air-fryer-chicken-thighs/"
   },
   {
      "title": "Happy Roast Chicken",
      "url": "https://www.allrecipes.com/recipe/214478/happy-roast-chicken/"
   }
]



# Setup Tools

In [29]:
# Tools 
from langchain.agents import Tool
from langchain.tools import BaseTool

# Chicken functions
def list_chicken_recipes(query: str):        
    return chickenDishList

list_chicken_recipes_tool = Tool(name='Chicken Recipes tool', func= list_chicken_recipes, description="This tools lists the available Chicken Recipes it returns a list of recipes with a TITLE and a URL where you can fetch the recipe.")

# Dessert functions
def list_dessert_recipes(query: str):        
    return dessertList

list_dessert_recipes_tool = Tool(name='Dessert Recipes tool', func=list_dessert_recipes, 
    description="This tools lists the available Dessert Recipes it returns a list of recipes with a TITLE and a URL where you can fetch the recipe.")

# Recipe fetcher functions
def get_recipe(url: str): 
    return get_recipe_as_json(url)

get_recipe_as_json_tool = Tool(name='Get a Recipe tool', func=get_recipe, description="""
    Useful for fetching a particular recipe, you can only fetch a recipe with it's url, you must get that using another tool
    It uses the https://schema.org/Recipe format to store it's recipes. 
    """)

# Tool list
tools = [list_chicken_recipes_tool, list_dessert_recipes_tool, get_recipe_as_json_tool]

In [30]:
print('Chicken dishes:')
for i in chickenDishList:
    print(i['title'])
    
print()
print('Desserts:')
for i in dessertList:
    print(i['title'])

Chicken dishes:
Crispy Roasted Chicken
Roasted Spatchcocked Chicken With Potatoes
Easy Baked Chicken Thighs
Crispy Baked Chicken Thighs
Crispy and Tender Baked Chicken Thighs
Million Dollar Chicken
Simple Whole Roasted Chicken
Beer Can Chicken
Air Fryer Chicken Thighs
Happy Roast Chicken

Desserts:
Chocolate Snack Cake
Charred Spiced Pears with Smoky Vanilla Cherry Sauce
Meringue Topped Banana Pudding
White Chocolate Cinnamon Toast Crunch Bars
Plum Cobbler for Two
Pumpkin Cheesecake Cookies
Chocolate Whipped Cottage Cheese
Nutella Ice Cream
3-Ingredient Banana Oatmeal Cookies
Caramel Apple Pie Cookies


In [44]:
from langchain.agents import load_tools
from langchain.agents import initialize_agent
from langchain.llms import OpenAI
from langchain.chat_models import ChatOpenAI

from langchain.agents import initialize_agent
llm = ChatOpenAI(temperature=0, model_name='gpt-4') # 'gpt-3.5-turbo'

agent = initialize_agent(
    agent="zero-shot-react-description", 
    tools=tools, 
    llm=llm,
    verbose=True,
    max_iterations=7,    
    return_intermediate_steps=True
)
system = "SYSTEM: If the answer is not in the tools or context passed to you then don't answer. If you don't know the answer then say so. QUESTION: " 
#agent.run("Can you show tell me what ingredients I need for the first baked chicken recipe? ")
#agent.run("Can you show tell me what ingredients I need for the last baked chicken recipe? ")
#agent.run("What is the best baked chicken recipe? Please look across all recipes with the word 'baked' in the title") # There are 3 baked chicken recipes
#agent.run("Is there a Chicken recipe that's prepared with an alchohol? And if so how long does it take in total from start time to finish?")
#agent.run("Which is healthier the Cheesecake or the beer chicken? Please explain how you got to your answer.")

#agent.run("What tools do I need for the Nutella Ice Cream?")
#agent.run("My bowl is broken, can I still make Nutella Ice Cream?")

#response = agent({"input": f"{system} Is the moon closer to earth or the sun?"})
response = agent({"input": f"{system} My bowl is broken, can I still make Nutella Ice Cream?"})

#print("################")
#print(print(response["intermediate_steps"]))





> Entering new AgentExecutor chain...
This question is about astronomy, which is not related to the tools I have access to. I don't have the information to answer this question.
Final Answer: I'm sorry, I don't have the information to answer this question.

> Finished chain.


In [46]:
print(response["intermediate_steps"])

[]


# UI

In [37]:
import gradio as gr

# # Import langchain stuff
# from langchain.agents import load_tools, initialize_agent, AgentType
# from langchain.llms import OpenAI


# # Initializing the LLM and the Toolset
# llm = OpenAI(temperature=0)
# tools = load_tools(["wikipedia"], llm=llm)
# agent = initialize_agent(tools, llm, agent=AgentType.ZERO_SHOT_REACT_DESCRIPTION, verbose=True)

def langchain_bot(prompt):
    if prompt:
        text = agent.run(prompt)
        return text
    return "Type a prompt to get a Wikipedia-like response!"

# Customize the appearance and style of the interface
iface = gr.Interface(fn=langchain_bot, inputs=gr.Textbox(lines=5, placeholder="Type your prompt here..."), 
                     outputs=gr.Textbox(), title="Wikipedia Langchain Bot 🦜",
                     description="Generate Wikipedia-like responses using Langchain AI.")

# Launch the interface
iface.launch()

Running on local URL:  http://127.0.0.1:7862

To create a public link, set `share=True` in `launch()`.




> Entering new AgentExecutor chain...
I need to find a recipe for ice cream using the Dessert Recipes tool.
Action: Dessert Recipes tool
Action Input: Ice cream
Observation: [{'title': 'Chocolate Snack Cake', 'url': 'https://www.allrecipes.com/chocolate-snack-cake-recipe-8350343'}, {'title': 'Charred Spiced Pears with Smoky Vanilla Cherry Sauce', 'url': 'https://www.allrecipes.com/charred-spiced-pears-with-smoky-vanilla-cherry-sauce-recipe-8347080'}, {'title': 'Meringue Topped Banana Pudding', 'url': 'https://www.allrecipes.com/meringue-topped-banana-pudding-recipe-8347040'}, {'title': 'White Chocolate Cinnamon Toast Crunch Bars', 'url': 'https://www.allrecipes.com/white-chocolate-cinnamon-toast-crunch-bars-recipe-7556790'}, {'title': 'Plum Cobbler for Two', 'url': 'https://www.allrecipes.com/plum-cobbler-for-two-recipe-8304143'}, {'title': 'Pumpkin Cheesecake Cookies', 'url': 'https://www.allrecipes.com/pumpkin-cheesecake-cookies-recipe-7972485'}, {'title': 'Chocolate Whipped Cottag